In [103]:
from GraphTsetlinMachine.graphs import Graphs
from GraphTsetlinMachine.tm import MultiClassGraphTsetlinMachine
from time import time
import argparse
from skimage.util import view_as_windows
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
import matplotlib

In [104]:
# Load the CSV file generated by C program
df = pd.read_csv('hex_game_results_13.csv')

# Limit to 10,000 rows(just for more speed processing)
df = df.iloc[:100000]

# Convert 'Moves' column to lists of integers
df['Moves'] = df['Moves'].apply(lambda x: list(map(int, x.split())))

# Check the processed moves
print("Processed Moves:")
print(df['Moves'].head())

# Assuming board size of 13x13 for the Hex game
BOARD_SIZE = 13

# Function to convert moves into a final board state
def get_final_board_state(moves, board_size):
    board = np.zeros((board_size, board_size), dtype=int)
    for i, move in enumerate(moves):
        player = 1 if i % 2 == 0 else 2
        row, col = move // board_size, move % board_size
        board[row, col] = player
    return board

# Add the final board state to the DataFrame
df['FinalBoard'] = df['Moves'].apply(lambda moves: get_final_board_state(moves, BOARD_SIZE))

# Check the final board states
print("Final Board State for the first game:")
print(df['FinalBoard'].iloc[0])
df['Winner']

Processed Moves:
0    [137, 54, 139, 138, 73, 75, 148, 130, 13, 135,...
1    [49, 29, 81, 0, 115, 104, 41, 40, 105, 76, 144...
2    [142, 139, 97, 56, 33, 110, 35, 167, 76, 48, 1...
3    [13, 158, 102, 49, 101, 54, 18, 71, 108, 26, 4...
4    [3, 51, 103, 95, 11, 165, 98, 47, 49, 46, 55, ...
Name: Moves, dtype: object
Final Board State for the first game:
[[2 1 2 1 1 0 1 2 1 1 2 2 2]
 [1 1 1 2 2 0 1 2 1 1 1 0 2]
 [2 2 2 1 2 2 1 2 0 1 1 0 1]
 [2 2 0 1 1 2 1 2 1 2 1 2 1]
 [1 0 2 1 2 2 0 2 1 2 2 1 2]
 [0 0 2 2 1 1 1 0 1 2 2 2 2]
 [1 1 1 2 2 2 2 1 1 2 1 0 1]
 [1 2 1 2 0 0 2 0 1 1 1 2 2]
 [2 2 1 0 2 2 0 0 1 2 1 2 2]
 [2 2 0 1 1 1 1 2 1 0 1 0 1]
 [2 2 0 1 1 2 2 1 2 1 1 2 1]
 [1 0 2 1 2 1 2 1 1 2 0 2 1]
 [1 1 2 1 2 1 2 2 1 0 1 0 2]]


0        1
1        1
2        2
3        2
4        2
        ..
99995    2
99996    2
99997    1
99998    1
99999    1
Name: Winner, Length: 100000, dtype: int64

In [105]:
# Prepare lists to store new x_train and y_train
new_x= []
new_y= []

# Loop over the DataFrame
for idx, row in df.iterrows():
    # Get the FinalBoard and Winner
    game_board = row['FinalBoard']
    winner = row['Winner']
    
    # Decompose the game into two binary boards (for Player 1 and Player 2)
    player1_board = (game_board == 1).astype(int)
    player2_board = (game_board == 2).astype(int)
    
    # Append to new_x_train (one game results in two boards)
    new_x.append(player1_board)
    new_x.append(player2_board)

    # For new_y, add two labels for each game:
    # - If Player 1 wins, add 0 (for both Player 1 and Player 2 boards)
    # - If Player 2 wins, add 1 (for both Player 1 and Player 2 boards)
    if winner == 1:
        new_y.append(0)  # For Player 1's board
        new_y.append(0)  # For Player 2's board
    elif winner == 2:
        new_y.append(1)  # For Player 1's board
        new_y.append(1)  # For Player 2's board

# Convert the new_x_train and new_y_train lists to numpy arrays
new_x = np.array(new_x)
new_y = np.array(new_y)

# Output the new structures
print(f"New x shape: {new_x.shape}")  # Should be (number_of_games, 2, 13, 13)
print(f"New y shape: {new_y.shape}")  # Should be twice the length of df['Winner']
print(f"New y values: {new_y}")       # Labels for the decomposed games

New x shape: (200000, 13, 13)
New y shape: (200000,)
New y values: [0 0 0 ... 0 0 0]


In [106]:
# Split the data into training and testing sets
split_index = int(0.8 * len(new_x))

# Split the data into training and test sets
x_train, x_test = new_x[:split_index], new_x[split_index:]
y_train, y_test = new_y[:split_index], new_y[split_index:]

# Output the shapes of the splits to confirm
print(f"x_train shape: {x_train.shape}")
print(f"x_test shape: {x_test.shape}")
print(f"y_train shape: {y_train.shape}")
print(f"y_test shape: {y_test.shape}")

x_train shape: (160000, 13, 13)
x_test shape: (40000, 13, 13)
y_train shape: (160000,)
y_test shape: (40000,)


In [107]:
x_train[0]

array([[0, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0, 0],
       [1, 1, 1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0],
       [0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 1, 0, 1],
       [0, 0, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1],
       [1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0],
       [0, 0, 0, 0, 1, 1, 1, 0, 1, 0, 0, 0, 0],
       [1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 1],
       [1, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0],
       [0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0],
       [0, 0, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1],
       [0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 1, 0, 1],
       [1, 0, 0, 1, 0, 1, 0, 1, 1, 0, 0, 0, 1],
       [1, 1, 0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 0]])

In [108]:
y_train[0]

0

In [109]:
from GraphTsetlinMachine.graphs import Graphs
import numpy as np
from GraphTsetlinMachine.tm import MultiClassGraphTsetlinMachine
from time import time


dim = 13

number_of_nodes = dim * dim


# Node values (binarized, so 0 or 1)
symbol_names = ['0', '1'] 

# Distance to walls (for a 13x13 grid, distances from 0 to 6)
for dist in range(dim // 2 + 1):
    symbol_names.append(f'DistToWall_{dist}')

# Adjacency to walls
symbol_names.extend(['TouchingRedWall', 'TouchingBlueWall'])

# Row and column information
for row in range(dim):
    symbol_names.append(f'Row_{row}')
for col in range(dim):
    symbol_names.append(f'Col_{col}')

symbol_names

['0',
 '1',
 'DistToWall_0',
 'DistToWall_1',
 'DistToWall_2',
 'DistToWall_3',
 'DistToWall_4',
 'DistToWall_5',
 'DistToWall_6',
 'TouchingRedWall',
 'TouchingBlueWall',
 'Row_0',
 'Row_1',
 'Row_2',
 'Row_3',
 'Row_4',
 'Row_5',
 'Row_6',
 'Row_7',
 'Row_8',
 'Row_9',
 'Row_10',
 'Row_11',
 'Row_12',
 'Col_0',
 'Col_1',
 'Col_2',
 'Col_3',
 'Col_4',
 'Col_5',
 'Col_6',
 'Col_7',
 'Col_8',
 'Col_9',
 'Col_10',
 'Col_11',
 'Col_12']

In [111]:
# Initialize the graph object with appropriate symbols and settings
graphs_train = Graphs(x_train.shape[0], symbols=symbol_names, hypervector_size=128, hypervector_bits=2)

# Step 2: Set the number of graph nodes for each training graph
for graph_id in range(x_train.shape[0]):
    graphs_train.set_number_of_graph_nodes(graph_id, dim * dim)

# Step 3: Prepare the node configuration
graphs_train.prepare_node_configuration()

# Step 4: Add nodes for each graph
for graph_id in range(x_train.shape[0]):
    for row in range(dim):
        for col in range(dim):
            node_id = row * dim + col  # Unique node ID for each hexagon

            # Dynamically calculate the number of neighbors for each node
            number_of_neighbors = 0
            if row > 0: number_of_neighbors += 1  # Above
            if row < dim - 1: number_of_neighbors += 1  # Below
            if col > 0: number_of_neighbors += 1  # Left
            if col < dim - 1: number_of_neighbors += 1  # Right
            if row > 0 and col < dim - 1: number_of_neighbors += 1  # AboveRight
            if row < dim - 1 and col > 0: number_of_neighbors += 1  # BelowLeft

            # Check for Node 0 (top-left corner)
            #if node_id == 0:
                #print(f"Node 0 (graph {graph_id}): number_of_neighbors = {number_of_neighbors}")
                # Ensure Node 0 has exactly 2 neighbors
                #assert number_of_neighbors == 2, f"Error: Node 0 has {number_of_neighbors} neighbors, expected 2."

            # define the nodes with the correct number of neighbors(dynamically)
            graphs_train.add_graph_node(graph_id, node_id, number_of_neighbors)

# Step 5: Add node properties for each graph
for graph_id in range(x_train.shape[0]):
    for row in range(dim):
        for col in range(dim):
            node_id = row * dim + col  # Unique node ID for each hexagon

            # Feature 1: Value of each node (convert to string)
            node_value = str(x_train[graph_id, row, col])
            if node_value in symbol_names:
                graphs_train.add_graph_node_property(graph_id, node_id, node_value)
            else:
                print(f"Warning: Node value {node_value} not found in symbol_names")

            # Feature 2: Distance to walls or center
            distance_to_wall = min(row, col, dim - row - 1, dim - col - 1)
            graphs_train.add_graph_node_property(graph_id, node_id, f'DistToWall_{distance_to_wall}')

            # Feature 3: Adjacency to walls
            if row == 0 or row == dim - 1:
                graphs_train.add_graph_node_property(graph_id, node_id, "TouchingRedWall")
            if col == 0 or col == dim - 1:
                graphs_train.add_graph_node_property(graph_id, node_id, "TouchingBlueWall")

            # Feature 4: Row and column information
            graphs_train.add_graph_node_property(graph_id, node_id, f'Row_{row}')
            graphs_train.add_graph_node_property(graph_id, node_id, f'Col_{col}')
# Step 6: Prepare the edge configuration for the training data
graphs_train.prepare_edge_configuration()

# Step 7: Add edges between nodes (neighboring hexagons) for the training data
for graph_id in range(x_train.shape[0]):
    for row in range(dim):
        for col in range(dim):
            node_id = row * dim + col

            # Handle Node 0 (top-left corner) separately to avoid adding too many edges
            if node_id == 0:
                # Node 0 can only connect to the right and below
                #print(f"Adding edges for Node 0 in graph {graph_id}")
                graphs_train.add_graph_node_edge(graph_id, node_id, node_id + dim, "Below")  # Connect to node below
                graphs_train.add_graph_node_edge(graph_id, node_id, node_id + 1, "Right")    # Connect to node on the right
                #print(f"Node 0 edges: Below -> {node_id + dim}, Right -> {node_id + 1}")
                continue  # Skip the rest of the logic for Node 0 to avoid adding more edges


            # Add edges to neighboring hexagons (hex grid has up to 6 neighbors per cell)
            if row > 0:  # Add edge to the hexagon above
                graphs_train.add_graph_node_edge(graph_id, node_id, node_id - dim, "Above")
            if row < dim - 1:  # Add edge to the hexagon below
                graphs_train.add_graph_node_edge(graph_id, node_id, node_id + dim, "Below")
            if col > 0:  # Add edge to the hexagon on the left
                graphs_train.add_graph_node_edge(graph_id, node_id, node_id - 1, "Left")
            if col < dim - 1:  # Add edge to the hexagon on the right
                graphs_train.add_graph_node_edge(graph_id, node_id, node_id + 1, "Right")

            # Optionally add diagonal neighbors (depending on your hex grid layout)
            if row > 0 and col < dim - 1:
                graphs_train.add_graph_node_edge(graph_id, node_id, node_id - dim + 1, "AboveRight")
            if row < dim - 1 and col > 0:
                graphs_train.add_graph_node_edge(graph_id, node_id, node_id + dim - 1, "BelowLeft")

In [112]:
# Check if node still has no edges (for debugging)
if not graphs_train.graph_node_id[graph_id][node_id]:
                print(f"Warning: Node {node_id} in graph {graph_id} has no edges added.")

In [113]:
# Step 8: After adding nodes and edges, encode the graph for the training data
graphs_train.encode()

print("Training data with new features produced")
print('finish')

Training data with new features produced
finish


In [114]:
# Initialize the graph object with appropriate symbols and settings
graphs_test = Graphs(x_test.shape[0], symbols=symbol_names, hypervector_size=128, hypervector_bits=2)

# Step 2: Set the number of graph nodes for each training graph
for graph_id in range(x_test.shape[0]):
    graphs_test.set_number_of_graph_nodes(graph_id, dim * dim)

# Step 3: Prepare the node configuration
graphs_test.prepare_node_configuration()

# Step 4: Add nodes for each graph
for graph_id in range(x_test.shape[0]):
    for row in range(dim):
        for col in range(dim):
            node_id = row * dim + col  # Unique node ID for each hexagon

            # Dynamically calculate the number of neighbors for each node
            number_of_neighbors = 0
            if row > 0: number_of_neighbors += 1  # Above
            if row < dim - 1: number_of_neighbors += 1  # Below
            if col > 0: number_of_neighbors += 1  # Left
            if col < dim - 1: number_of_neighbors += 1  # Right
            if row > 0 and col < dim - 1: number_of_neighbors += 1  # AboveRight
            if row < dim - 1 and col > 0: number_of_neighbors += 1  # BelowLeft

            # Check for Node 0 (top-left corner)
            #if node_id == 0:
                #print(f"Node 0 (graph {graph_id}): number_of_neighbors = {number_of_neighbors}")
                # Ensure Node 0 has exactly 2 neighbors
                #assert number_of_neighbors == 2, f"Error: Node 0 has {number_of_neighbors} neighbors, expected 2."

            # define the nodes with the correct number of neighbors(dynamically)
            graphs_test.add_graph_node(graph_id, node_id, number_of_neighbors)

# Step 5: Add node properties for each graph
for graph_id in range(x_test.shape[0]):
    for row in range(dim):
        for col in range(dim):
            node_id = row * dim + col  # Unique node ID for each hexagon

            # Feature 1: Value of each node (convert to string)
            node_value = str(x_test[graph_id, row, col])
            if node_value in symbol_names:
                graphs_test.add_graph_node_property(graph_id, node_id, node_value)
            else:
                print(f"Warning: Node value {node_value} not found in symbol_names")

            # Feature 2: Distance to walls or center
            distance_to_wall = min(row, col, dim - row - 1, dim - col - 1)
            graphs_test.add_graph_node_property(graph_id, node_id, f'DistToWall_{distance_to_wall}')

            # Feature 3: Adjacency to walls
            if row == 0 or row == dim - 1:
                graphs_test.add_graph_node_property(graph_id, node_id, "TouchingRedWall")
            if col == 0 or col == dim - 1:
                graphs_test.add_graph_node_property(graph_id, node_id, "TouchingBlueWall")

            # Feature 4: Row and column information
            graphs_test.add_graph_node_property(graph_id, node_id, f'Row_{row}')
            graphs_test.add_graph_node_property(graph_id, node_id, f'Col_{col}')
# Step 6: Prepare the edge configuration for the training data
graphs_test.prepare_edge_configuration()

# Step 7: Add edges between nodes (neighboring hexagons) for the training data
for graph_id in range(x_test.shape[0]):
    for row in range(dim):
        for col in range(dim):
            node_id = row * dim + col

            # Handle Node 0 (top-left corner) separately to avoid adding too many edges
            if node_id == 0:
                # Node 0 can only connect to the right and below
                #print(f"Adding edges for Node 0 in graph {graph_id}")
                graphs_test.add_graph_node_edge(graph_id, node_id, node_id + dim, "Below")  # Connect to node below
                graphs_test.add_graph_node_edge(graph_id, node_id, node_id + 1, "Right")    # Connect to node on the right
                #print(f"Node 0 edges: Below -> {node_id + dim}, Right -> {node_id + 1}")
                continue  # Skip the rest of the logic for Node 0 to avoid adding more edges


            # Add edges to neighboring hexagons (hex grid has up to 6 neighbors per cell)
            if row > 0:  # Add edge to the hexagon above
                graphs_test.add_graph_node_edge(graph_id, node_id, node_id - dim, "Above")
            if row < dim - 1:  # Add edge to the hexagon below
                graphs_test.add_graph_node_edge(graph_id, node_id, node_id + dim, "Below")
            if col > 0:  # Add edge to the hexagon on the left
                graphs_test.add_graph_node_edge(graph_id, node_id, node_id - 1, "Left")
            if col < dim - 1:  # Add edge to the hexagon on the right
                graphs_test.add_graph_node_edge(graph_id, node_id, node_id + 1, "Right")

            # Optionally add diagonal neighbors (depending on your hex grid layout)
            if row > 0 and col < dim - 1:
                graphs_test.add_graph_node_edge(graph_id, node_id, node_id - dim + 1, "AboveRight")
            if row < dim - 1 and col > 0:
                graphs_test.add_graph_node_edge(graph_id, node_id, node_id + dim - 1, "BelowLeft")

# Step 8: After adding nodes and edges, encode the graph for the training data
graphs_test.encode()

print("Test data with new features produced")

Test data with new features produced


In [120]:
# Create the Graph Tsetlin Machine model
tm = MultiClassGraphTsetlinMachine(
    number_of_clauses=2000,  # Adjust based on complexity of the game
    T=2000,
    s=10.0,
    depth=1,
    message_size=256,
    message_bits=2,
    max_included_literals=64
)

# Train the model on the Hex game data
for i in range(20):  # Number of epochs
    start_training = time()
    tm.fit(graphs_train, y_train, epochs=1, incremental=True)
    stop_training = time()

    print(f"Epoch {i + 1} completed in {stop_training - start_training:.2f} seconds")

# Evaluate the model
# Assuming you have similarly prepared graphs_test for test data
start_testing = time()
result_test = 100 * (tm.predict(graphs_test) == y_test).mean()
stop_testing = time()

print(f"Test accuracy: {result_test:.2f}%")

Initialization of sparse structure.
Epoch 1 completed in 32.06 seconds
Epoch 2 completed in 27.38 seconds
Epoch 3 completed in 27.45 seconds
Epoch 4 completed in 27.64 seconds
Epoch 5 completed in 27.80 seconds
Epoch 6 completed in 27.82 seconds
Epoch 7 completed in 27.79 seconds
Epoch 8 completed in 27.57 seconds
Epoch 9 completed in 27.55 seconds
Epoch 10 completed in 27.52 seconds
Epoch 11 completed in 28.02 seconds
Epoch 12 completed in 27.48 seconds
Epoch 13 completed in 27.55 seconds
Epoch 14 completed in 27.52 seconds
Epoch 15 completed in 27.92 seconds
Epoch 16 completed in 27.92 seconds
Epoch 17 completed in 27.57 seconds
Epoch 18 completed in 27.66 seconds
Epoch 19 completed in 27.89 seconds
Epoch 20 completed in 27.85 seconds
Test accuracy: 48.55%


In [116]:
output = np.array(y_test[:20])

# Grouping every two consecutive elements and mapping to Player 1 or Player 2
merged_output = []
for i in range(0, len(output), 2):
    if output[i:i+2].tolist() == [1, 1]:
        merged_output.append(2)  # Player 2 wins
    elif output[i:i+2].tolist() == [0, 0]:
        merged_output.append(1)  # Player 1 wins

# Convert the result to a numpy array
merged_output = np.array(merged_output)

# Print the result
print("First 10 actual winners in Y_test:")
print(merged_output)

First 10 actual winners in Y_test:
[2 1 1 1 1 1 1 2 1 2]


In [121]:
# Step 1: Predict the winners using the trained model
Y_pred = tm.predict(graphs_test)

output_pred = np.array(Y_pred[:20])

# Grouping every two consecutive elements and mapping to Player 1 or Player 2
merged_output_pred = []
for i in range(0, len(output_pred), 2):
    if output_pred[i:i+2].tolist() == [1, 1]:
        merged_output_pred.append(2)  # Player 2 wins
    elif output_pred[i:i+2].tolist() == [0, 0]:
        merged_output_pred.append(1)  # Player 1 wins

# Convert the result to a numpy array
merged_output_pred = np.array(merged_output_pred)

# Print the result
print("First 10 predicted winners in Y_pred:")
print(merged_output_pred)
print(min(merged_output_pred))
print(max(merged_output_pred))

First 10 predicted winners in Y_pred:
[2 2 2 2 2 2 2 2 2 2]
2
2


In [118]:
weights = tm.get_state()[1].reshape(2, -1)
for i in range(tm.number_of_clauses):
        print("Clause #%d W:(%d %d)" % (i, weights[0,i], weights[1,i]), end=' ')
        l = []
        for k in range(128 * 2):
            if tm.ta_action(0, i, k):
                if k < 128:
                    l.append("x%d" % (k))
                else:
                    l.append("NOT x%d" % (k - 128))
        print(" AND ".join(l))



Clause #0 W:(-1 4) x23 AND x30 AND x52 AND x89 AND NOT x23 AND NOT x88 AND NOT x90 AND NOT x120
Clause #1 W:(-3 2) x28 AND x30 AND x75 AND x85 AND x91 AND x112 AND NOT x4 AND NOT x6 AND NOT x9 AND NOT x28 AND NOT x29 AND NOT x37 AND NOT x45 AND NOT x59 AND NOT x60 AND NOT x70 AND NOT x124
Clause #2 W:(1 0) x33 AND x68 AND NOT x33 AND NOT x88
Clause #3 W:(1 -5) x42 AND x55 AND x98 AND x113 AND x118 AND NOT x1 AND NOT x3 AND NOT x5 AND NOT x6 AND NOT x9 AND NOT x11 AND NOT x13 AND NOT x18 AND NOT x20 AND NOT x22 AND NOT x23 AND NOT x26 AND NOT x32 AND NOT x36 AND NOT x41 AND NOT x45 AND NOT x53 AND NOT x58 AND NOT x59 AND NOT x61 AND NOT x63 AND NOT x64 AND NOT x65 AND NOT x67 AND NOT x69 AND NOT x72 AND NOT x75 AND NOT x80 AND NOT x83 AND NOT x84 AND NOT x88 AND NOT x89 AND NOT x91 AND NOT x92 AND NOT x95 AND NOT x98 AND NOT x100 AND NOT x102 AND NOT x103 AND NOT x104 AND NOT x106 AND NOT x107 AND NOT x109 AND NOT x110 AND NOT x116 AND NOT x121 AND NOT x125 AND NOT x127
Clause #4 W:(2 1

In [119]:
print(tm.number_of_clauses)

20000
